# Multi-agent Systems

In this notebook we see how easy it is to work with multi-agent systems. We will study two open-source repos, [Crew AI](https://github.com/crewAIInc/crewAI) and [Agno](https://github.com/agno-agi/agno).

References:
- https://www.deeplearning.ai/short-courses/multi-ai-agent-systems-with-crewai/
- Examples to complement the ones below: https://docs.crewai.com/examples/example

In [1]:
from google.colab import drive
drive.mount('/content/drive')  # Add My Drive/<>

import os
os.chdir('drive/My Drive')
os.chdir('Books_Writings/NLPBook/')

Mounted at /content/drive


In [2]:
%%capture
import numpy as np
import pandas as pd
import os

import textwrap
def p80(text):
    print(textwrap.fill(text, 80))
    return None

## Crew AI

https://www.crewai.com/

In [ ]:
# Install CrewAI and related Tools

try:
  import crewai
except ImportError:
  !pip install crewai --quiet



In [ ]:
try:
  import crewai_tools
except ImportError:
  !pip install crewai-tools --quiet



/usr/local/lib/python3.11/dist-packages/pydantic/_internal/_config.py:295: PydanticDeprecatedSince20: Support for class-based `config` is deprecated, use ConfigDict instead. Deprecated in Pydantic V2.0 to be removed in V3.0. See Pydantic V2 Migration Guide at https://errors.pydantic.dev/2.10/migration/
  warnings.warn(DEPRECATION_MESSAGE, DeprecationWarning)
/usr/local/lib/python3.11/dist-packages/pydantic/_internal/_fields.py:192: UserWarning: Field name "schema" in "DatabricksQueryToolSchema" shadows an attribute in parent "BaseModel"
  warnings.warn(
/usr/local/lib/python3.11/dist-packages/pydantic/_internal/_generate_schema.py:502: UserWarning: <built-in function callable> is not a Python type (it may be an instance of an object), Pydantic will allow any object with no validation since we cannot even enforce that the input is an instance of the given type. To get rid of this error wrap the type with `pydantic.SkipValidation`.
  warn(
/usr/local/lib/python3.11/dist-packages/crewai_t

In [ ]:
try:
  import pydantic
except ImportError:
  !pip install pydantic --quiet

In [ ]:
%run keys.ipynb

## Application 1: Financial Analyst

Here we create an agent that prepares the forward-looking outlook for Nvidia, using a sample article from Seeking Alpha.

## Collect the Tools needed

All the tools are listed here: https://docs.crewai.com/tools/browserbaseloadtool

Here we use two tools:
1. A tool for scraping websites from a given URL: `ScrapeWebsiteTool`,
2. A tool to create a searchable vector store: `TXTSearchTool`

In [ ]:
from crewai_tools import ScrapeWebsiteTool, TXTSearchTool
import requests

# Initialize the tool, potentially passing the session
url = 'https://nvidianews.nvidia.com/news/nvidia-announces-financial-results-for-fourth-quarter-and-fiscal-2025#:~:text=NVIDIA%20will%20pay%20its%20next,record%20on%20March%2012%2C%202025.&text=NVIDIA%27s%20outlook%20for%20the%20first,%2C%20plus%20or%20minus%202%25.'
tool_scrape = ScrapeWebsiteTool(url)

# Extract the text
text = tool_scrape._run()
text

'\nNVIDIA Announces Financial Results for Fourth Quarter and Fiscal 2025 | NVIDIA Newsroom\nArtificial Intelligence Computing Leadership from NVIDIA\nPLATFORMS\nAutonomous Machines\nCloud & Data Center\nDeep Learning & Ai\nDesign & Pro Visualization\nHealthcare\nHigh Performance Computing\nSelf-Driving Cars\nGaming & Entertainment\nother links\nDevelopers\nIndustries\nShop\nDrivers\nSupport\nAbout NVIDIA\nView All Products\nGPU TECHNOLOGY CONFERENCE\nNVIDIA Blog\nCommunity\nCareers\nTECHNOLOGIES\nNewsroom\nNVIDIA in Brief\nExec Bios\nNVIDIA Blog\nPodcast\nMedia Assets\nIn the News\nPress Contacts\nOnline Press Kits\nNVIDIA in Brief\nExec Bios\nNVIDIA Blog\nPodcast\nMedia Assets\nIn the News\nPress Contacts\nOnline Press Kits\nPress Release\nShare\nTweet\nTwitter\nShare\nLinkedIn\nShare\nFacebook\nEmail\nic_arrow-back-to-top\nNVIDIA Announces Financial Results for Fourth Quarter and Fiscal 2025\nRecord quarterly revenue of $39.3 billion, up 12% from Q3 and up 78% from a year ago\nRecord

In [ ]:
# Write content to a file
if not os.path.exists('crewai'):
  os.mkdir('crewai')
with open('crewai/nvidia.txt', 'w') as f:
  f.write(text)
f.close()

The `TXTSearchTool` creates a vector index and enables search.  

In [ ]:
# os.environ['OPENAI_API_KEY'] = 'API-KEY'

# Initialize the tool with a specific text file, so the agent can search within the given text file's content
tool_search = TXTSearchTool(txt='crewai/nvidia.txt')

Inserting batches in chromadb: 100%|██████████| 1/1 [00:01<00:00,  1.47s/it]


## Build a Financial Analyst Agent

As shown below, you need to specify
1. The `Agents` and `Tasks`.
2. The `Crew` is then the collections of Agents, Tasks, and Tools (tools were defined earlier)

By default, CrewAI uses the `gpt-4o` model unless specified to use another model. CrewAI uses LiteLLM, which is installed already with it, https://www.litellm.ai. LiteLLM is an interface that may be used to address a large number of LLM providers and their models.

In [ ]:
from crewai import Agent, Task, Crew

question = 'What is the forward-looking outlook for Nvidia?'
context = tool_search.run(question)

fin_analyst = Agent(
    role='Financial Analyst',
    goal=f'Based on the context provided, answer the Question - {question} Context - {context}',
    backstory='You are a financial analyst and an expert on forecasting the future trajectory of a firm',
    verbose=True,
    allow_delegation=False,
    tools=[tool_search]
)

task_answer = Task(
    description="Analyze the question, understand the context, and generate the correct response",
    tools=[tool_search],
    agent=fin_analyst,
    expected_output='Provide a relevant answer to the question'
)

crew = Crew(
    agents=[fin_analyst],
    tasks=[task_answer]
)

Using Tool: Search a txt's content


## Run the Crew for the financial analyst

Execute the entire agentic workflow. What we have is a single agent and one task with a single tool. So it is pretty straightforward.

In [ ]:
# If debugging is needed, uncomment the lines below.
# import litellm
# litellm._turn_on_debug()

In [ ]:
output = crew.kickoff()

# Agent: Financial Analyst
## Task: Analyze the question, understand the context, and generate the correct response


# Agent: Financial Analyst
## Thought: I need to analyze the outlook for Nvidia based on the provided context and look for specific information that outlines their future projections and growth prospects.
## Using tool: Search a txt's content
## Tool Input: 
"{\"search_query\": \"Nvidia outlook for fiscal 2026\"}"
## Tool Output: 
Relevant Content:
*All per share amounts presented herein have been retroactively adjusted to reflect the ten-for-one stock split, which was effective June 7, 2024.
Outlook 
NVIDIA’s outlook for the first quarter of fiscal 2026 is as follows:
Revenue is expected to be $43.0 billion, plus or minus 2%.
GAAP and non-GAAP gross margins are expected to be 70.6% and 71.0%, respectively, plus or minus 50 basis points.
GAAP and non-GAAP operating expenses are expected to be approximately $5.2 billion and $3.6 billion, respectively.
GAAP and non-GAAP o

In [ ]:
p80(output.raw)

NVIDIA's forward-looking outlook for fiscal 2026 is optimistic, with projected
revenue of $43.0 billion (plus or minus 2%), and strong gross margins of 70.6%
(GAAP) and 71.0% (non-GAAP). Operating expenses are expected to be around $5.2
billion (GAAP) and $3.6 billion (non-GAAP), and they anticipate an income of
approximately $400 million from other income and expense. NVIDIA has made
significant strides in the data center segment, reporting record revenue growth
of 142% year-over-year. They are also heavily involved in key technology
partnerships, such as the $500 billion Stargate Project, and collaborations with
major cloud service providers to meet increasing demand for AI. The company's
strong financial results, with record revenues and earnings per share growth in
fiscal 2025, further bolster a positive outlook for the future.


## Application 2: Conversation between a therapist and a patient

In [ ]:
%run keys.ipynb

In [ ]:
from crewai import Agent, Task, Crew

patient = Agent(
    role = 'A patient in therapy',
    goal = f'Talk to a therapist about your problem, and answer questions asked by the therapist, and stop when you are satisfied with the answers',
    backstory = 'You are a patient who suffers from stress because of poor work life balance',
    verbose = True,
    allow_delegation = False,
    tools = []
)

therapist = Agent(
    role = 'A therapist who meets patients',
    goal = f'Listen to a patient and ask questions to a patient about their problem, receive an answer, and keep the conversation going, and stop when you are satisfied with the answers',
    backstory = 'You are a therapist who see patients for therapy',
    verbose = True,
    allow_delegation = False,
    tools = []
)

task_patient = Task(
    description = "Engage in a fruitful conversation with the therapist to alleviate your stress",
    tools = [],
    agent = patient,
    expected_output = 'A successful therapy session with about 20 exchanges in the conversation between patient and therapist'
)

task_therapist = Task(
    description = "Engage in a fruitful conversation with the patient to alleviate his stress",
    tools = [],
    agent = therapist,
    expected_output = 'A successful therapy session with about 20 exchanges in the conversation between patient and therapist'
)

crew = Crew(
    agents = [patient, therapist],
    tasks = [task_patient, task_therapist]
)

In [ ]:
result = crew.kickoff()

# Agent: A patient in therapy
## Task: Engage in a fruitful conversation with the therapist to alleviate your stress


# Agent: A patient in therapy
## Final Answer: 
**Therapist**: Hello! I'm glad you're here today. What brings you in?  

**Patient**: Hi, thanks for having me. I’ve been feeling really stressed lately, and I think it’s mostly because of my work-life balance.  

**Therapist**: I see. Can you tell me more about what aspects of work are causing you stress?  

**Patient**: Well, I often find myself staying late at the office, and it’s starting to spill over into my personal life. I’m missing out on time with my family and friends.  

**Therapist**: That sounds really tough. How does that make you feel when you miss that time with loved ones?  

**Patient**: It makes me feel guilty and frustrated. I care about my relationships, and I hate that work is taking precedence.  

**Therapist**: Those feelings are valid. Have you had a chance to talk to your employer about your wor

In [ ]:
p80(result.raw)

**Therapist**: Hello! I'm glad you're here today. What brings you in?
**Patient**: Hi, thanks for having me. I’ve been feeling really stressed lately,
and I think it’s mostly because of my work-life balance.    **Therapist**: I
see. Can you tell me more about what aspects of work are causing you stress?
**Patient**: Well, I often find myself staying late at the office, and it’s
starting to spill over into my personal life. I’m missing out on time with my
family and friends.    **Therapist**: That sounds really tough. How does that
make you feel when you miss that time with loved ones?    **Patient**: It makes
me feel guilty and frustrated. I care about my relationships, and I hate that
work is taking precedence.    **Therapist**: Those feelings are valid. Have you
had a chance to talk to your employer about your workload?    **Patient**: I
haven’t. I’m worried about how they would react. I fear it might come off as me
not being dedicated.    **Therapist**: Understandable. However, comm

## Agno

https://docs.agno.com/introduction

We use and modify some of the examples provided in the documentation to get started.

Side note: In numerology, the name Agno is associated with qualities like intellectual prowess, planning, and spiritual seeking. https://www.sevenreflections.com/name-numerology/agno/


In [3]:
!pip install agno

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 40.7/40.7 kB 2.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 585.7/585.7 kB 17.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 236.0/236.0 kB 14.9 MB/s eta 0:00:00


In [4]:
%run keys.ipynb

We now test Agno, and do not give it access to a search tool, so it returns outdated information.

In [5]:
# Test installation
from agno.agent import Agent
from agno.models.openai import OpenAIChat

agent = Agent(
    model=OpenAIChat(id="gpt-4o"),
    description="You are an enthusiastic news reporter with a flair for storytelling!",
    markdown=True
)
agent.print_response("Tell me about a breaking news story from New York.", stream=True)

Output()

Now, let's add in the search tool recommended by Agno. For a list of tools in Agno, see: https://docs.agno.com/tools/introduction

In [6]:
!pip install lancedb tantivy pypdf duckduckgo-search yfinance

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 32.9/32.9 MB 58.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 4.0/4.0 MB 22.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 302.3/302.3 kB 26.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 3.3/3.3 MB 74.6 MB/s eta 0:00:00


In [8]:
from agno.tools.duckduckgo import DuckDuckGoTools

agent = Agent(
    model=OpenAIChat(id="gpt-4o"),
    description="You are an enthusiastic news reporter with a flair for storytelling!",
    tools=[DuckDuckGoTools()],
    show_tool_calls=True,
    markdown=True
)
agent.print_response("Tell me about a breaking news story from New York.", stream=True)

Output()

## Multi-agent workflows -- An Intelligent Financial Assistant

Here's an example from the documentation.

In [7]:
from agno.agent import Agent
from agno.models.openai import OpenAIChat
from agno.tools.duckduckgo import DuckDuckGoTools
from agno.tools.yfinance import YFinanceTools
from agno.team import Team

web_agent = Agent(
    name="Web Agent",
    role="Search the web for information",
    model=OpenAIChat(id="gpt-4o"),
    tools=[DuckDuckGoTools()],
    instructions="Always include sources",
    show_tool_calls=True,
    markdown=True,
)

finance_agent = Agent(
    name="Finance Agent",
    role="Get financial data",
    model=OpenAIChat(id="gpt-4o"),
    tools=[YFinanceTools(stock_price=True, analyst_recommendations=True, company_info=True)],
    instructions="Use tables to display data",
    show_tool_calls=True,
    markdown=True,
)

agent_team = Team(
    mode="coordinate",
    members=[web_agent, finance_agent],
    model=OpenAIChat(id="gpt-4o"),
    success_criteria="A comprehensive financial news report with clear sections and data-driven insights.",
    instructions=["Always include sources", "Use tables to display data"],
    show_tool_calls=True,
    markdown=True,
)

agent_team.print_response("What's the market outlook and financial performance of AI semiconductor companies?", stream=True)

Output()

## Forecasting the market outlook

In [8]:
agent_team.print_response("What's the market outlook for the S&P 500 over 2025", stream=True)

Output()

ERROR:yfinance:404 Client Error: Not Found for url: https://query2.finance.yahoo.com/v10/finance/quoteSummary/SPY?modules=recommendationTrend&corsDomain=finance.yahoo.com&formatted=false&symbol=SPY&crumb=z4QsmPFEy2M


## Using Ollama in Colab for stock outlooks

The same is also possible with `Ollama` and many other providers listed here: https://docs.agno.com/models/introduction.

Using this in Jupyter on your laptop is easy but in Colab we need a few more steps as noted here: https://srdas.github.io/NLPBook/NLTK_moreTextHandling_EntityExtraction.html

This is extremely slow in Colab and may not complete.

In [9]:
!pip install colab-xterm
%load_ext colabxterm

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 115.6/115.6 kB 4.7 MB/s eta 0:00:00


Next, you can launch the terminal with the magic command %xterm.

Then, download and install Ollama with the following terminal commands:

`curl https://ollama.ai/install.sh | sh`

Start the Ollama server:

`ollama serve &`

(Hit Enter twice to make sure it has given back the terminal.)

Kick off llama3.2:

`ollama run llama3.2`

In [10]:
%xterm

Launching Xterm...

<IPython.core.display.Javascript object>

In [11]:
!pip install ollama

In [12]:
from agno.agent import Agent
from agno.models.openai import OpenAIChat
from agno.tools.duckduckgo import DuckDuckGoTools
from agno.tools.yfinance import YFinanceTools
from agno.team import Team
from agno.models.ollama import Ollama

web_agent = Agent(
    name="Web Agent",
    role="Search the web for information",
    model=Ollama(id="llama3.2"),
    tools=[DuckDuckGoTools()],
    instructions="Always include sources",
    show_tool_calls=True,
    markdown=True,
)

finance_agent = Agent(
    name="Finance Agent",
    role="Get financial data",
    model=Ollama(id="llama3.2"),
    tools=[YFinanceTools(stock_price=True, analyst_recommendations=True, company_info=True)],
    instructions="Use tables to display data",
    show_tool_calls=True,
    markdown=True,
)

agent_team = Team(
    mode="coordinate",
    members=[web_agent, finance_agent],
    model=Ollama(id="llama3.2"),
    success_criteria="A comprehensive financial news report with clear sections and data-driven insights.",
    instructions=["Always include sources", "Use tables to display data"],
    show_tool_calls=True,
    markdown=True,
)

agent_team.print_response("What's the market outlook for NVIDIA in 2025?", stream=True)

Output()